# `pandas`

[`pandas`](https://pandas.pydata.org) is a data analysis library build on top of [NumPy](https://www.numpy.org/) and other Python libraries.
It organises data using `DataFrame`s and provides tools to analyse and visualise them.

In [ ]:
import numpy as np
import pandas as pd

We'll use `pandas` to explore the [e-mail campaign data](https://blog.minethatdata.com/2008/03/minethatdata-e-mail-analytics-and-data.html) made available by Kevin Hillstrom.
We start by loading the data.

In [ ]:
hillstrom = pd.read_csv('hillstrom.csv')

We can inspect the first five rows using the function `head()`.

In [ ]:
hillstrom.head()

**Question**: how would you print the first ten rows?

**Question**: how would you print the last five rows?

`DataFrame`s also have `shape` and `dtypes` attribute.

In [ ]:
hillstrom.shape

In [ ]:
hillstrom.dtypes

**Note**: unlike Excel spreadsheets, *all* values in a column must be of the same type: for example, you cannot mix numbers and text.

# Selecting rows and columns

## Selecting rows

You can select rows that satisfy certain conditions using the slicing operator `[]` and a `list` of Boolean values.

In [ ]:
hillstrom[hillstrom['visit'] == 1].head()

**Note**: `pandas` has its own set of logical operators!

| Python    | `pandas`                    |
|:----------|:----------------------------|
| `x and y` | `(x) & (y)`                 |
| `x or y`  | <code>(x) &#124; (y)</code> |
| `not x`   | `~ x`                       |

In [ ]:
hillstrom[
    (hillstrom['mens'] == 1) &
    (hillstrom['womens'] == 1)
].head()

**Question**: what does the condition below select?

In [ ]:
hillstrom[
    (hillstrom['conversion'] == 1) &
    ~(hillstrom['visit'] == 1)
].head()

## Selecting columns

You can select specific columns by name using the slicing operator `[]` with a string.

In [ ]:
hillstrom['recency'].head()

What's the type of the column we've just selected?

In [ ]:
type(hillstrom['recency'])

You can select multiple columns using the slicing operator `[]` and a `list` of strings.

In [ ]:
hillstrom[['mens', 'womens']].head()  # Two square brackets: slicing operator + list

## Selecting rows and columns simultaneously

The function `loc()` can be used to simultaneously select rows and columns.

In [ ]:
hillstrom.loc[:, 'recency'].head()

In [ ]:
hillstrom.loc[:, ['mens', 'womens']].head()

In [ ]:
hillstrom.loc[hillstrom['newbie'] == 1, ['visit', 'conversion']].head()

**Question**: what does the code below compute?

In [ ]:
hillstrom.loc[(hillstrom['channel'] == 'Web') & (hillstrom['segment'] != 'No E-mail'), 'spend'].mean()

# Summarising and visualising a single variable

When dealing with lots of data, it's often convenient to summarise variables using a few relevant numbers or visualise their distributions, rather than scrolling through huge spreadsheets to try and make sense of the data.

**Note**: before we start, we need to configure Jupyter so that plots will be shown inside the notebook.

In [ ]:
%matplotlib inline

**Question**: what are some commonly used numbers and plots that can be used to summarise the distribution of variables?

## Continuous variables

Continuous variables represent *numerical quantities*.
For example, the variable `history` represents the total USD value spent in the past year by each customer.

The distribution of a continuous variable is commonly visualised using a histogram.

In [ ]:
hillstrom['history'].plot.hist(color='darkblue')

**Question**: how does the number of bins change your perception of the shape of the distribution? Try plotting a histogram with 20 bins.

Alternatively, the distribution of a continuous variable can also be visualised using a density plot.

In [ ]:
hillstrom['history'].plot.density(color='darkblue')

The 'centre' of the distribution is commonly summarised using the mean or the median, whereas its 'spread' can be described in terms of standard deviation (or variance) or order statistics such as the quartiles.

In addition to individual functions such as `mean()` and `median()`, `pandas` provides a handy `describe()` function.

In [ ]:
hillstrom['history'].describe()

**Question**: what happens if you call `describe()` on the `DataFrame` rather than a single column?

## Categorical variables

Categorical variables represent *groups* or quantities that can only take a small number of distinct values.
For example, the variable `zip_code` is a classification of ZIP (post) codes in three categories.

The distribution of a categorical variable can be summarised by *tabulating*, i.e. counting the number of observations in each category.

In [ ]:
hillstrom['zip_code'].value_counts()

**Question**: how would you get proportions rather than counts?

The tabulation can also be visualised using a bar plot.

In [ ]:
hillstrom['zip_code'].value_counts().plot.bar(color='darkblue')

## Exercise

Go through the other variables in `hillstrom` and:
1. Decide if they are continuous or categorical
1. Summarise and plot their distributions

Did you find anything curious?

# Summarising and visualising multiple variables

Whilst summarising and visualising single variables can give us some insights into the data we're working with, we're often interested in understanding *relationships* between multiple variables.

## Two continuous variables

The relationship between two continuous variables is commonly visualised using a scatter plot.

In [ ]:
hillstrom.plot.scatter(x='history', y='spend')

In addition, *linear* relationships can be summarised using the (Pearson) correlation coefficient.

In [ ]:
hillstrom[['history', 'spend']].corr()

## Two categorical variables

The relationship between two categorical variables can be summarised by *cross-tabulating*.

In [ ]:
pd.crosstab(hillstrom['segment'], hillstrom['visit'])

**Question**: how would you get proportions rather than counts?

Cross-tabulation can also be achieved using the function `groupby()`, which provides a more general method known as [split-apply-combine](http://pandas.pydata.org/pandas-docs/stable/groupby.html):
1. First, observations are split into groups defined by one or more categorical variables
2. Then, a summary function such as `mean()` is applied within each group independently
3. Finally, results are combined back into a `DataFrame`

![Split-apply-combine](http://i.imgur.com/yjNkiwL.png)

In [ ]:
hillstrom.groupby('segment')['visit'].mean()

We can now turn these proportions into a bar plot.

In [ ]:
hillstrom.groupby('segment')['visit'].mean().sort_values().plot.bar(color='darkblue')

## One continuous and one categorical variable

The relationship between a continuous and a categorical variable can be visualised by *grouping* observations on the latter, and summarising or plotting the former.

In [ ]:
hillstrom.groupby(['segment', 'zip_code'])['history'].mean()

In [ ]:
hillstrom.groupby(['segment', 'zip_code'])['history'].describe()

Alternatively, the function `pivot_table()` can be used to produce spreadsheet-style pivot tables.

In [ ]:
hillstrom.pivot_table(values='history', index='segment', columns='zip_code')

**Question**: how would you compute medians in each group?

The distribution in each group can be visualised using a box-and-whisker plot.

In [ ]:
hillstrom.boxplot(column='history', by=['segment', 'zip_code'], rot=45)

## Exercise

Your boss has asked you to investigate which e-mail campaign performed the best, particularly regarding:
1. How much incremental sales per customer did they drive?
1. Did they perform differently across customer segments?
1. Which segments should be targeted going forward?

Use the data in `hillstrom` to answer these questions — and feel free to come up with more!

Did you find anything curious?